In [22]:
import geopandas as gpd
import numpy as np
import altair as alt
alt.data_transformers.disable_max_rows()
pass

In [143]:
lt = gpd.read_feather("data.feather")
vilnius =lt[(lt['GYV_PAV'] == 'Vilniaus m.') & (lt['POP'] >= 100)].copy()
vilnius['logPop'] = np.log(vilnius['POP'])

In [146]:
alt.Chart(vilnius).mark_bar().encode(
    alt.X("logPop", title='log(Population)').bin(maxbins=20), 
    alt.Y("count()", title='count')
).properties(title="Population density in Vilnius")

alt.Chart(...)

In [147]:
vilnius['pct_children'] = vilnius['all_00_14'].fillna(0) / vilnius['POP']
vilnius['pct_retired'] = vilnius['all_65_plius'].fillna(0) / vilnius['POP']
vilnius['pct_male'] = vilnius['MALE'].fillna(0) / vilnius['POP']
vilnius['pct_unemployed'] = vilnius['ACT_unemployed'].fillna(0) / vilnius['POP']
vilnius['pct_upper_education'] = vilnius['EDUC_H_all'].fillna(0) / vilnius['POP']

vilnius['pct_manager_specialist'] = (
    vilnius['PRF_clerics'].fillna(0) + vilnius['PRF_managers'].fillna(0) + 
    vilnius['PRF_professionals'].fillna(0)
) / vilnius['POP']
vilnius['pct_employers'] = vilnius['OCP_employer'].fillna(0) / vilnius['POP']

col_names = [
    'POP', 'logPop', 'pct_children', 'pct_retired', 'pct_male', 
    'pct_unemployed', 'pct_upper_education', 'pct_manager_specialist', 'pct_employers',
    'geometry'
]
data_for_clustering = vilnius[col_names].copy()
data_for_clustering['logPopNorm'] = (data_for_clustering['logPop'] - data_for_clustering['logPop'].min())  / (data_for_clustering['logPop'].max() - data_for_clustering['logPop'].min())

In [148]:
import pydeck as pdk
layers = [    
    pdk.Layer(
        "GeoJsonLayer",
        data=data_for_clustering,    
        get_fill_color="[255 * (1 - pct_upper_education), 255* (1 - pct_manager_specialist) ,255* (1 - pct_children)]",
        pickable=True,
        auto_highlight = True,
    ),
]

In [149]:
pdk.Deck(
    layers,
    tooltip=True,
    initial_view_state=pdk.ViewState(
        longitude=25.25,
        latitude=54.7,
        zoom=10,
        min_zoom=5,
        max_zoom=15,    
    )
).to_html(iframe_width=720)